In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
import numpy as np
from keras.preprocessing.text import Tokenizer

Using TensorFlow backend.


In [2]:
from google.colab import files
files.upload()

Saving Sentiment_train.tsv to Sentiment_train.tsv


{'Sentiment_train.tsv': b"PhraseId\tSentenceId\tPhrase\tSentiment\n1\t1\tA series of escapades demonstrating the adage that what is good for the goose is also good for the gander , some of which occasionally amuses but none of which amounts to much of a story .\t1\n2\t1\tA series of escapades demonstrating the adage that what is good for the goose\t2\n3\t1\tA series\t2\n4\t1\tA\t2\n5\t1\tseries\t2\n6\t1\tof escapades demonstrating the adage that what is good for the goose\t2\n7\t1\tof\t2\n8\t1\tescapades demonstrating the adage that what is good for the goose\t2\n9\t1\tescapades\t2\n10\t1\tdemonstrating the adage that what is good for the goose\t2\n11\t1\tdemonstrating the adage\t2\n12\t1\tdemonstrating\t2\n13\t1\tthe adage\t2\n14\t1\tthe\t2\n15\t1\tadage\t2\n16\t1\tthat what is good for the goose\t2\n17\t1\tthat\t2\n18\t1\twhat is good for the goose\t2\n19\t1\twhat\t2\n20\t1\tis good for the goose\t2\n21\t1\tis\t2\n22\t1\tgood for the goose\t3\n23\t1\tgood\t3\n24\t1\tfor the goose\t2\

In [0]:
df=pd.read_csv("Sentiment_train.tsv",quoting=3,header=0,delimiter="\t")

In [18]:
df.head()

PhraseId  SentenceId                                             Phrase  \
0         1           1  A series of escapades demonstrating the adage ...   
1         2           1  A series of escapades demonstrating the adage ...   
2         3           1                                           A series   
3         4           1                                                  A   
4         5           1                                             series   

   Sentiment  
0          1  
1          2  
2          2  
3          2  
4          2

In [0]:
x=df.Phrase
y=df.Sentiment

In [0]:
x_train,x_test,y_train,y_test=train_test_split(x,y,test_size=0.35,random_state=123)


In [0]:
topwords=10000                         # Vocab size(Unique words)

In [0]:
t=Tokenizer(num_words=topwords)

In [0]:
t.fit_on_texts(x_train.tolist())
x_train=t.texts_to_sequences(x_train.tolist())
x_test=t.texts_to_sequences(x_test.tolist())

In [24]:
print(len(x_train))
print(len(x_test))
print(len(y_test))
print(len(y_train))

101439
54621
54621
101439


In [0]:
review_length=100                                                                  # each review will have maximum 80 words in it

In [0]:
embedding_vector_length=50                                                        # each word is represented by 40 numbers

In [0]:
from keras.models import Sequential
from keras.layers import Dense,Dropout,Flatten,Embedding
from keras.preprocessing import sequence

In [0]:
X_train=sequence.pad_sequences(x_train,maxlen=review_length,padding="post")       # padding is done to make each review in equal length
X_test=sequence.pad_sequences(x_test,maxlen=review_length,padding="post")         # padding="post"--unequal review will be filled with 0 at the end

In [0]:
model=Sequential()

In [0]:
model.add(Embedding(topwords+1,
                  embedding_vector_length,                                        # each word is represented by 40 numbers
                   input_length=review_length))

In [0]:
model.add(Flatten())

In [0]:
model.add(Dense(300,activation="relu",input_shape=(100,)))

In [0]:
model.add(Dropout(0.30))                                                         # Dropout some neurones to overcome overfitting

In [0]:
model.add(Dense(200,activation="relu"))

In [0]:
model.add(Dropout(0.20))

In [0]:
model.add(Dense(150,activation="relu"))

In [0]:
model.add(Dropout(0.10))

In [0]:
model.add(Dense(90,activation="relu"))

In [0]:
model.add(Dense(30,activation="relu"))

In [0]:
model.add(Dense(5,activation="softmax"))                                          # Softmax for classification

In [0]:
from keras.utils import to_categorical                                            # converting each sentiment into unique category
y_train=to_categorical(y_train,num_classes=5)

In [0]:
y_test=to_categorical(y_test,num_classes=5)                                       # converting each sentiment into unique category

In [0]:
model.compile(optimizer="adam",loss="categorical_crossentropy",metrics=['accuracy'])

In [65]:
model.fit(X_train,y_train,epochs=10,
          batch_size=64,validation_data=(X_test,y_test))

Train on 101439 samples, validate on 54621 samples
Epoch 1/10
101439/101439 [==============================] - 83s 816us/step - loss: 0.4943 - acc: 0.8108 - val_loss: 1.1114 - val_acc: 0.6187
Epoch 2/10
101439/101439 [==============================] - 84s 829us/step - loss: 0.4524 - acc: 0.8272 - val_loss: 1.1730 - val_acc: 0.6097
Epoch 3/10
101439/101439 [==============================] - 83s 816us/step - loss: 0.4172 - acc: 0.8387 - val_loss: 1.2526 - val_acc: 0.6166
Epoch 4/10
101439/101439 [==============================] - 84s 828us/step - loss: 0.3889 - acc: 0.8482 - val_loss: 1.3693 - val_acc: 0.6104
Epoch 5/10
101439/101439 [==============================] - 83s 820us/step - loss: 0.3647 - acc: 0.8556 - val_loss: 1.5391 - val_acc: 0.6064
Epoch 6/10
101439/101439 [==============================] - 84s 831us/step - loss: 0.3458 - acc: 0.8613 - val_loss: 1.6049 - val_acc: 0.6126
Epoch 7/10
101439/101439 [==============================] - 84s 831us/step - loss: 0.3262 - acc: 0.8672

In [66]:
print(model.predict(X_test[:2]))     # It outputs probabilities for five classes

[[7.4077356e-03 1.0586063e-01 8.1783271e-01 6.4915866e-02 3.9830832e-03]
 [9.9999321e-01 6.8105310e-06 1.4180216e-16 2.8275136e-25 2.9999496e-30]]


In [67]:
y_test[:2]

array([[0., 0., 1., 0., 0.],
       [1., 0., 0., 0., 0.]], dtype=float32)